In [390]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import linear_kernel, cosine_similarity
from stop_words import get_stop_words
import numpy as np
stop_words_rus = get_stop_words('russian')

In [391]:
import sqlite3

def get_book_by_id(id1):
    bs = sqlite3.connect('pasha_bookstore.db')
    bs.row_factory = sqlite3.Row
    row = bs.execute(f'SELECT * FROM Books WHERE id={id1}').fetchall()[0]

    book = {
        'id': row['id'] if row['id'] != None else '',
        'author': row['author'] if row['author'] != None else '',
        'genre': row['genre'] if row['genre'] != None else '',
        'tags': row['tags'] if row['tags'] != None else '',
        'distances': row['distances'] if row['distances'] != None else ''
    }

    return book

In [392]:
def get_all_ids():
    bs = sqlite3.connect('pasha_bookstore.db')
    ids = bs.execute(f'SELECT id FROM Books').fetchall()
    return [id[0] for id in ids]

books = []
arr_id = get_all_ids()
k = 0
for book_id in arr_id:
    books.append(get_book_by_id(book_id))
    books[k]['tags'] = books[k]['tags'].replace(' ','')
    books[k]['tags'] = books[k]['tags'].replace(',',' ')
    books[k]['author'] = books[k]['author'].rstrip('.- ') + ' '
    books[k]['genre'] = books[k]['genre'].replace(' ','')
    books[k]['genre'] = books[k]['genre'].replace(',',' ')
    books[k]['genre'] = books[k]['genre'].replace('.',' ')
    k+=1

In [393]:
def get_book_by_id2(book_id):
    return books[book_id]

In [394]:
def get_tags_prof(book_id):
    book = books[book_id]
    return book['author'] + book['tags']

In [395]:
def get_tags_fic(book_id):
    book = books[book_id]
    return book['author'] + book['tags'] + book['genre']

In [396]:
def get_cos_fic(id1,id2):
    tf = TfidfVectorizer(analyzer='word',ngram_range=(1, 1),min_df=0, stop_words=stop_words_rus)
    tg1 = get_tags_fic(id1)
    print(tg1)
    tg2 = get_tags_fic(id2)
    print(tg2)
    meta = [tg1,tg2]
    tfidf_matrix = tf.fit_transform(meta)
    return linear_kernel(tfidf_matrix, tfidf_matrix)[0,1]

In [397]:
def get_cos_prof(id1,id2):
    tf = TfidfVectorizer(analyzer='word',ngram_range=(1, 1),min_df=0, stop_words=stop_words_rus)
    tg1 = get_tags_prof(id1)
    tg2 = get_tags_prof(id2)
    meta = [tg1,tg2]
    tfidf_matrix = tf.fit_transform(meta)
    return linear_kernel(tfidf_matrix, tfidf_matrix)[0,1]

In [398]:
def set_distances(id1, distances):
    bs = sqlite3.connect('pasha_bookstore.db')
    bs.execute(f'UPDATE Books SET distances=\'{distances}\' WHERE id=\'{id1}\'')
    bs.commit()
    bs.close()
    return

In [399]:
cos_matrix = np.ndarray((25000,25000))
def cosine_db_books():
    for i in range(len(books)):
        book1 = books[i]
        cos_dict = {}
        for j in range(len(books)):
            if (i == j):
                continue
            book2 = books[j]
            if (i > j):
                if cos_matrix[j][i] > 0:
                    cos_dict[j] = cos_matrix[j][i]
            else:
                if (book1['genre'] == book2['genre'] == 'Профессиональная литература'):
                    cos_matrix[i][j] = round(get_cos_prof(i,j) , 4)
                    if cos_matrix[i][j] > 0:
                        cos_dict[j] = round(cos_matrix[i][j],4)
                elif ((book1['genre'] == 'Профессиональная литература') | (book2['genre'] == 'Профессиональная литература')):
                    cos_matrix[i][j] = 0
                else:
                    cos_matrix[i][j] = round(get_cos_fic(i,j) , 4)
                    if (cos_matrix[i][j] > 0):
                        cos_dict[j] = cos_matrix[i][j]
        k = 0
        str_cos = ''
        for key, value in sorted(cos_dict.items(), key=lambda item: item[1], reverse = True):
            k += 1
            if value == 0.0:
                break
            str_cos += str(key) + ' '
            str_cos += str(value) + ' '
            if (k == 100):
                break
        set_distances(books[i]['id'], str_cos)
        books[i]['distances'] = str_cos
    return
        

In [400]:
def add_book_cos_prof(book):
    #по id получаем книгу, у каждой книги есть массив cos 100 штук, массив id книг 100 штук, уже отсортированные
    i = 0
    n = len(b_arr)
    book_rec = []
    s1 = get_tags_prof(book)# в бд еще закинуть
    for b in b_arr:
        if (b['genre'] != 'проф'):
            continue
        с = get_cos_prof(book,b)
        book_rec.append(c)
        for i in range(len(b['cos'])):
            if (c > b['cos'][i]):
                b['ids_rec'][i] = n
                b['cos']
        #не дописано ААААААААААААААААААААА

In [401]:
def get_recommendations_onbook(book_id,k,ids_already_read):
    book = books[book_id]
    s = book['distances'].split()
    n = len(s)//2
    d = {}
    for i in range(n):
        d[int(s[2*i])] = float(s[2*i+1])
    id_rec = []
    kol = 0
    for key, value in sorted(d.items(), key=lambda item: item[1], reverse = True):
        if (key not in ids_already_read):
            kol += 1
            id_rec.append(key)
            if (kol == k):
                break
    return id_rec

In [402]:
#book = {
    #id
    #genres
    #author
    #tags
    #строка с расстояниями
#}

In [403]:
def get_recommendations_user(id_arr,kol,ids_already_read):
    d = {}
    if (len(id_arr) <=10):
        for book_id in id_arr:
            d.update(get_recommendations_onbook(book_id,20,ids_already_read))
    elif (len(id_arr) <= 20):
        for book_id in id_arr:
            d.update(get_recommendations_onbook(book_id,10,ids_already_read))
    elif (len(id_arr) > 20):
        for book_id in id_arr:
            d.update(get_recommendations_onbook(book_id,5,ids_already_read))
    it = 0
    id_rec = []
    for key, value in sorted(d.items(), key=lambda item: item[1], reverse = True):
        it+=1
        id_rec.append(key)
        if (kol == it):
            break
    return id_rec

In [404]:
def process_user(id_arr):
    return get_recommendation_user(id_arr,5,id_arr)

In [405]:
#def process_reg_rate(id):
    #по id книгу
    #добавление в id_arr пользователя

In [406]:
def update_av_rate(book_id,rate):
    #получаю книгу по id
    #добавляю оценку к сумме оценок книги
    #инкремент кол-ва оценок книги
    return

In [407]:
def parse_search(search):
    search = search.lower()
    search = search.replace('.',' ')
    d = {}
    for i in range(len(books)):
        if (get_book_by_id(book_id)['genre'] == 'Профессиональная литература'):
            tg = get_tags_prof(book_id)
        else:
            tg = get_tags_fic(book_id)
        meta = [tg,search]
        tfidf_matrix = tf.fit_transform(meta)
        d[arr_id] = linear_kernel(tfidf_matrix, tfidf_matrix)[0,1]
    result = []
    k = 0
    for key, value in sorted(d.items(), key=lambda item: item[1], reverse = True):
        k+=1
        result.append(key)
        if (k == 10):
            break
    return result

# Books on russian

In [408]:
get_book_by_id(1)['distances']

'1 0.5031 2 0.5031 4 0.5031 5 0.5031 6 0.5031 7 0.5031 8 0.5031 9 0.5031 3 0.3563 '

In [409]:
cosine_db_books()

Букс Н Биографии Мемуары
Верник В Биографии Мемуары
Букс Н Биографии Мемуары
Разумовский Л.С Биографии Мемуары
Букс Н Биографии Мемуары
Феррас Родригу Карлуш Биографии Мемуары
Букс Н Биографии Мемуары
Маяковский В.В Биографии Мемуары
Букс Н Биографии Мемуары
Ратнер А.Г Биографии Мемуары
Букс Н Биографии Мемуары
Бесли Э Биографии Мемуары
Букс Н Биографии Мемуары
Симмонс С Биографии Мемуары
Букс Н Биографии Мемуары
Крофт М Биографии Мемуары
Букс Н Биографии Мемуары
Рокфеллер Д Биографии Мемуары
Букс Н Биографии Мемуары
Свечин Н Детектив Остросюжетнаялитература
Букс Н Биографии Мемуары
Мальцев А Детектив Остросюжетнаялитература
Букс Н Биографии Мемуары
Донцова Д.А Детектив Остросюжетнаялитература
Букс Н Биографии Мемуары
Маринина А Детектив Остросюжетнаялитература
Букс Н Биографии Мемуары
Силвис Р Детектив Остросюжетнаялитература
Букс Н Биографии Мемуары
Браун Д Детектив Остросюжетнаялитература
Букс Н Биографии Мемуары
Данфорд К Детектив Остросюжетнаялитература
Букс Н Биографии Мемуары
Си

Букс Н Биографии Мемуары
Александрова Наталья Детектив Остросюжетнаялитература
Букс Н Биографии Мемуары
Донцова Д.А Детектив Остросюжетнаялитература
Букс Н Биографии Мемуары
Николсон Д Детектив Остросюжетнаялитература
Букс Н Биографии Мемуары
Литвинова А.В., Литвинов С.В Детектив Остросюжетнаялитература
Букс Н Биографии Мемуары
Хиггинс Кларк М Детектив Остросюжетнаялитература
Букс Н Биографии Мемуары
Маринина А Детектив Остросюжетнаялитература
Букс Н Биографии Мемуары
Володарская О Детектив Остросюжетнаялитература
Букс Н Биографии Мемуары
Кинг С Мистика Ужасы
Букс Н Биографии Мемуары
Кинг С Мистика Ужасы
Букс Н Биографии Мемуары
Варго А Мистика Ужасы
Букс Н Биографии Мемуары
Кинг С Мистика Ужасы
Букс Н Биографии Мемуары
Мид Р Мистика Ужасы
Букс Н Биографии Мемуары
Кинг С Мистика Ужасы
Букс Н Биографии Мемуары
Кинг С Мистика Ужасы
Букс Н Биографии Мемуары
Кинг С Мистика Ужасы
Букс Н Биографии Мемуары
Страуд Д Мистика Ужасы
Букс Н Биографии Мемуары
Кинг С Мистика Ужасы
Букс Н Биографии М

Верник В Биографии Мемуары
Левина Л.Т Профессиональнаялитература
Верник В Биографии Мемуары
Лавров С Профессиональнаялитература
Верник В Биографии Мемуары
Левина Л.Т Профессиональнаялитература
Верник В Биографии Мемуары
Леонтьев В.П Профессиональнаялитература
Верник В Биографии Мемуары
Васильев А.Н Профессиональнаялитература
Верник В Биографии Мемуары
Шоу З Профессиональнаялитература
Верник В Биографии Мемуары
Пол Бэрри Профессиональнаялитература
Верник В Биографии Мемуары
Рой О Мистика Ужасы
Верник В Биографии Мемуары
Алендер К Мистика Ужасы
Верник В Биографии Мемуары
Кинг С Мистика Ужасы
Верник В Биографии Мемуары
Алендер К Мистика Ужасы
Верник В Биографии Мемуары
Лавкрафт Г Мистика Ужасы
Верник В Биографии Мемуары
Вега Д Мистика Ужасы
Верник В Биографии Мемуары
Кинг С Мистика Ужасы
Верник В Биографии Мемуары
Кинг С Мистика Ужасы
Верник В Биографии Мемуары
Кинг С Мистика Ужасы
Верник В Биографии Мемуары
Кинг С Мистика Ужасы
Верник В Биографии Мемуары
Уэллс Г Фантастиказарубежная
Верн

Верник В Биографии Мемуары
Бушар С Русскаяклассическаяисовременнаялитература
Верник В Биографии Мемуары
Визбор Ю.И Русскаяклассическаяисовременнаялитература
Верник В Биографии Мемуары
Дезомбре Д Русскаяклассическаяисовременнаялитература
Верник В Биографии Мемуары
Аствацатуров А.А Русскаяклассическаяисовременнаялитература
Верник В Биографии Мемуары
Акунин Б.(Брусникин А.) Русскаяклассическаяисовременнаялитература
Верник В Биографии Мемуары
Бестер А Фантастиказарубежная
Верник В Биографии Мемуары
Лем С Фантастиказарубежная
Верник В Биографии Мемуары
Райаниеми Х Фантастиказарубежная
Верник В Биографии Мемуары
Оливер Л., Мандел Э Фантастиказарубежная
Верник В Биографии Мемуары
Грин С Фантастиказарубежная
Верник В Биографии Мемуары
Сапковский А Фантастиказарубежная
Верник В Биографии Мемуары
Бардуго Л Фантастиказарубежная
Верник В Биографии Мемуары
Пратчетт Т Фантастиказарубежная
Верник В Биографии Мемуары
Кейт Л Фантастиказарубежная
Верник В Биографии Мемуары
Толкин Д.Р.Р Фантастиказарубеж

Разумовский Л.С Биографии Мемуары
Стругацкий А.Н., Стругацкий Б Фантастикаотечественная
Разумовский Л.С Биографии Мемуары
Стругацкий А.Н., Стругацкий Б Фантастикаотечественная
Разумовский Л.С Биографии Мемуары
Казанцев К Детектив Остросюжетнаялитература
Разумовский Л.С Биографии Мемуары
Данилова А.В Детектив Остросюжетнаялитература
Разумовский Л.С Биографии Мемуары
Крамер М Детектив Остросюжетнаялитература
Разумовский Л.С Биографии Мемуары
Калинина Д.А Детектив Остросюжетнаялитература
Разумовский Л.С Биографии Мемуары
Андреева Н.В Детектив Остросюжетнаялитература
Разумовский Л.С Биографии Мемуары
Солнцева Наталья Детектив Остросюжетнаялитература
Разумовский Л.С Биографии Мемуары
Донцова Д.А Детектив Остросюжетнаялитература
Разумовский Л.С Биографии Мемуары
Полякова Т.В Детектив Остросюжетнаялитература
Разумовский Л.С Биографии Мемуары
Михалкова Е.И Детектив Остросюжетнаялитература
Разумовский Л.С Биографии Мемуары
Донцова Д.А Детектив Остросюжетнаялитература
Разумовский Л.С Биографии М

...

Пратчетт Т Фантастиказарубежная
Злотников Р.В Фантастикаотечественная
Пратчетт Т Фантастиказарубежная
Стругацкий А.Н., Стругацкий Б Фантастикаотечественная
Пратчетт Т Фантастиказарубежная
Гончарова Г.Д Фантастикаотечественная
Пратчетт Т Фантастиказарубежная
Злотников Р. В Фантастикаотечественная
Пратчетт Т Фантастиказарубежная
Каменские Юрий и Вера Фантастикаотечественная
Пратчетт Т Фантастиказарубежная
Тармашев С.С Фантастикаотечественная
Пратчетт Т Фантастиказарубежная
Сакрытина М.Н Фантастикаотечественная
Пратчетт Т Фантастиказарубежная
Головачёв В.В Фантастикаотечественная
Пратчетт Т Фантастиказарубежная
Лисина А Фантастикаотечественная
Пратчетт Т Фантастиказарубежная
Михайловский А.Б., Харников А Фантастикаотечественная
Пратчетт Т Фантастиказарубежная
Силлов Д.О Фантастикаотечественная
Уэйт У Фантастиказарубежная
Вейер Энди Фантастиказарубежная
Уэйт У Фантастиказарубежная
Сапковский А Фантастиказарубежная
Уэйт У Фантастиказарубежная
Конторович А.С Фантастикаотечественная
Уэйт У Фа

Гончарова Г.Д Фантастикаотечественная
Конторович А.С Фантастикаотечественная
Злотников Р. В Фантастикаотечественная
Конторович А.С Фантастикаотечественная
Каменские Юрий и Вера Фантастикаотечественная
Конторович А.С Фантастикаотечественная
Тармашев С.С Фантастикаотечественная
Конторович А.С Фантастикаотечественная
Сакрытина М.Н Фантастикаотечественная
Конторович А.С Фантастикаотечественная
Головачёв В.В Фантастикаотечественная
Конторович А.С Фантастикаотечественная
Лисина А Фантастикаотечественная
Конторович А.С Фантастикаотечественная
Михайловский А.Б., Харников А Фантастикаотечественная
Конторович А.С Фантастикаотечественная
Силлов Д.О Фантастикаотечественная
Тармашев С.С Фантастикаотечественная
Тармашев С.С Фантастикаотечественная
Тармашев С.С Фантастикаотечественная
Ковальчук А.А Фантастикаотечественная
Тармашев С.С Фантастикаотечественная
Голубева А. (Альфина) Фантастикаотечественная
Тармашев С.С Фантастикаотечественная
Ланцов М.А Фантастикаотечественная
Тармашев С.С Фантастикаоте

Ланцов М.А Фантастикаотечественная
Михайловский А.Б., Харников А Фантастикаотечественная
Ланцов М.А Фантастикаотечественная
Прозоров А Фантастикаотечественная
Ланцов М.А Фантастикаотечественная
Левицкий А Фантастикаотечественная
Ланцов М.А Фантастикаотечественная
Силлов Д.О Фантастикаотечественная
Ланцов М.А Фантастикаотечественная
Боталова М.Н Фантастикаотечественная
Ланцов М.А Фантастикаотечественная
Крапивин В.П Фантастикаотечественная
Ланцов М.А Фантастикаотечественная
Глуховский Д.А Фантастикаотечественная
Ланцов М.А Фантастикаотечественная
Ланцов М Фантастикаотечественная
Ланцов М.А Фантастикаотечественная
Хант Д Фантастикаотечественная
Ланцов М.А Фантастикаотечественная
Наумов К.В Фантастикаотечественная
Ланцов М.А Фантастикаотечественная
Злотников Р.В Фантастикаотечественная
Ланцов М.А Фантастикаотечественная
Стругацкий А.Н., Стругацкий Б Фантастикаотечественная
Ланцов М.А Фантастикаотечественная
Гончарова Г.Д Фантастикаотечественная
Ланцов М.А Фантастикаотечественная
Злотников

Прозоров А Фантастикаотечественная
Каменские Юрий и Вера Фантастикаотечественная
Прозоров А Фантастикаотечественная
Тармашев С.С Фантастикаотечественная
Прозоров А Фантастикаотечественная
Сакрытина М.Н Фантастикаотечественная
Прозоров А Фантастикаотечественная
Головачёв В.В Фантастикаотечественная
Прозоров А Фантастикаотечественная
Лисина А Фантастикаотечественная
Прозоров А Фантастикаотечественная
Михайловский А.Б., Харников А Фантастикаотечественная
Прозоров А Фантастикаотечественная
Силлов Д.О Фантастикаотечественная
Левицкий А Фантастикаотечественная
Силлов Д.О Фантастикаотечественная
Левицкий А Фантастикаотечественная
Боталова М.Н Фантастикаотечественная
Левицкий А Фантастикаотечественная
Крапивин В.П Фантастикаотечественная
Левицкий А Фантастикаотечественная
Глуховский Д.А Фантастикаотечественная
Левицкий А Фантастикаотечественная
Ланцов М Фантастикаотечественная
Левицкий А Фантастикаотечественная
Хант Д Фантастикаотечественная
Левицкий А Фантастикаотечественная
Наумов К.В Фантас

Наумов К.В Фантастикаотечественная
Стругацкий А.Н., Стругацкий Б Фантастикаотечественная
Наумов К.В Фантастикаотечественная
Гончарова Г.Д Фантастикаотечественная
Наумов К.В Фантастикаотечественная
Злотников Р. В Фантастикаотечественная
Наумов К.В Фантастикаотечественная
Каменские Юрий и Вера Фантастикаотечественная
Наумов К.В Фантастикаотечественная
Тармашев С.С Фантастикаотечественная
Наумов К.В Фантастикаотечественная
Сакрытина М.Н Фантастикаотечественная
Наумов К.В Фантастикаотечественная
Головачёв В.В Фантастикаотечественная
Наумов К.В Фантастикаотечественная
Лисина А Фантастикаотечественная
Наумов К.В Фантастикаотечественная
Михайловский А.Б., Харников А Фантастикаотечественная
Наумов К.В Фантастикаотечественная
Силлов Д.О Фантастикаотечественная
Злотников Р.В Фантастикаотечественная
Стругацкий А.Н., Стругацкий Б Фантастикаотечественная
Злотников Р.В Фантастикаотечественная
Гончарова Г.Д Фантастикаотечественная
Злотников Р.В Фантастикаотечественная
Злотников Р. В Фантастикаотечест

## Пример оценки схожести книг по их ключевым словам

In [ ]:
genre_arr = []
bool_arr = []
book_reg_arr = []
for i in range(len(genre_arr)):
    bool_arr[i] = False
for i in range(len(books)):
    for j in range(len(genre_arr)):
        if ((bool_arr[j] == False) & (books[i]['genre'] == genre_arr[j])):
            book_reg_arr.append(book[i])
            bool_arr[j] = True
#Получили массив самых популярных книг по жанру
    

In [ ]:
def reg(chosen_genres_arr):
    id_arr = []
    for i in range(len(book_reg_arr)):
        if (book_reg_arr[i]['genre'] in chosen_genres_arr):
            id_arr.append(book_reg_arr[i]['id'])